# Kapitel 4: Statistische Datenanalyse II – Parameterschätzung (Teil 3)

## Parameterunsicherheiten

In der Parameterschätzung wird unterschieden zwischen einer Punktschätzung und einer Intervallschätzung. Die **Punktschätzung** liefert lediglich einen Schätzwert $\hat{\mathbf{a}}$ für den Parametervektor $\mathbf{a}$ der Modellfunktion. Darüber hinaus ist aber ein Unsicherheitsintervall für den Parameter von Interesse, als ein aus Daten konstruiertes Konfidenzintervall, so dass im Sinne der frequentistischen Statistik ein bestimmter Anteil (z. B. 68,3%) aller Intervalle den wahren Wert enthalten. Diese Prozedur wird als **Intervallschätzung** bezeichnet. Dieses Intervall könnte beidseitig sein (salopp formuliert: "Parameter liegt zwischen...") oder einseitig ("Parameter ist kleiner als" oder "Parameter ist größer als"). In der modernen mathematischen Statistik werden dazu fast immer Maximum-Likelihood-Methoden eingesetzt; diese gehen allerdings über dieses Kurses hinaus und werden nur im Ausblick am Ende von Kapitel 4 kurz beleuchtet. In diesem Kapitel beschränken wir uns darauf, die Varianz des Schätzwerts innerhalb der Methode der kleinsten Quadrate (LS-Methode, auch: $\chi^2$-Methode) zu bestimmen.

### Varianz des Schätzwerts anschaulich
Anhand des analytisch lösbaren Beispiels einer wiederholten Messung einer Größe wollen einen Zusammenhang zwischen der Varianz des Schätzwerts für diese Größe und der Summe der Residuenquadrate $S$ herstellen. Wir nehmen dazu an, dass wir $N$ Messungen $y_i$ einer konstanten Größe mit dem wahren Wert $a=3$ durchführen. Damit ist die Modellfunktion $\lambda(a)$ eine konstante Funktion und für deren Wert für die $i$-te Messung gilt: $\lambda_i \equiv \lambda = a$. Da alle Messungen dieselbe Grundgesamtheit betreffen, ist die Varianz in jeder dieser Messungen gleich: $\sigma_i \equiv\sigma=1$. Nach der Methode der kleinsten Quadrate schätzen wir den Parameter, indem wir die Summe der Residuenquadrate $S$ minimieren:
$$
S\equiv\chi^2=\sum_i \frac{(y_i-a)^2}{\sigma^2} \overset{!}{=} \mathsf{min}
$$
Im ersten Teil dieses Kapitels finden Sie ein Codebeispiel mit einer Animation, in der mögliche Werte von $a$ in diese Gleichung eingesetzt und jeweils den Wert von $S$ gegen $a$ aufgetragen werden ("Parameterscan"). Die Frage, wie genau der Schätzwert $\hat{a}$ bekannt ist, wird durch die Bestimmung seiner Varianz $\mathsf{V}[\hat{a}]$ beantwortet. Es ist instruktiv, sich den Funktionsgraphen von $S(a)$ für eine Schätzung aus mehr und mehr Datenpunkten anzusehen. Mithilfe der linearen Fortpflanzung der Unsicherheit (Nebenrechnung folgt) erwarten wir, dass die Varianz $\mathsf{V}[\hat{a}]$ mit $N$ Messungen um einen Faktor $1/N$ schrumpft (und damit die Standardabweichung um $1/\sqrt{N}$ abnimmt), also 
$$
\mathsf{V}[\hat{a}] = \frac{\sigma^2}{N}.
$$

>**Nebenrechnung**
>
>Die Varianz von $\hat{a}$ lässt sich mithilfe der linearen Fortpflanzung der Unsicherheit berechnen. Da es sich um eine lineare Modellfunktion handelt, ist das Ergebnis exakt:
>$$
\mathsf{V}[\hat a] = \sum_j \left( \frac{\partial \hat a}{\partial y_j}\right)^2 \cdot \sigma_j^2.
>$$
>Wie weiter oben gezeight, ist der Schätzwert $\hat{a}$ gegeben durch den gewichteten Mittelwert der Messwerte mit den Gewichten $w_i = 1/\sigma_i^2$:
>$$
\hat a = \frac{1}{\sum_i w_i} \sum_i w_i y_i =
\frac{1}{\sum_i 1/\sigma_i^2} \sum_i \frac{y_i}{\sigma_i^2}.
>$$
>Mit den partiellen Ableitung von $\hat{a}$ nach den $y_i$
>$$
\frac{\partial \hat a}{\partial y_j} = \frac{1}{\sum_i 1/\sigma_i^2} \frac{1}{\sigma_j^2}
>$$
>ergibt sich für die Varianz von $\hat{a}$, unter der Annahme, dass alle Varianzen gleich sind:
>$$
\mathsf{V}[\hat a] = \frac{1}{(\sum_i 1/\sigma_i^2)^2} \sum_j \frac{\sigma_j^2}{\sigma_j^4} = \frac{1}{\sum_i 1/\sigma_i^2}\overset{\sigma_i \equiv \sigma}{=} \frac{\sigma^2}{N}.
>$$

Dies ist im folgenden Codebeispiel implementiert:

In [ ]:
"""least squares: sum of residuals adding more and more data"""

import numpy as np
import matplotlib.pyplot as plt

def LeastSquares_S( model, sigma, data ):
	"""least squares: function to compute squared sum of residuals"""

	# use np.meshgrid to process arrays of models applied on the same data
	MODEL, DATA = np.meshgrid( model, data )
	return np.sum( ( ( DATA - MODEL ) / sigma )**2, axis=0 )

# true model parameters
atrue = 3
sig   = 1

# scan of a values
amin, amax, steps = 0., 6., 300
a = np.linspace( amin, amax, steps )

# data points
N = 5
xi = np.linspace( 1, N, N )
xrange = np.linspace( 0.5, N + 0.5, steps )

rng = np.random.default_rng( 42 )
yi = rng.normal( loc=atrue, scale=sig, size=N )

fig,ax = plt.subplots( 2, N, figsize=(25,10) )

for i in np.arange( len( yi ) ):

	# compute S(a) with first i+1 data points
	S_plot = LeastSquares_S( a, sig, yi[:i+1] )
	
	# plot data points
	ax[0][i].errorbar( xi[:i+1], yi[:i+1], yerr=sig, fmt="ro" )
	ax[0][i].set_xlabel( r"$x$")
	ax[0][i].set_ylabel( r"$y$")
	ax[0][i].set_xlim( 0, 6 )
	ax[0][i].set_ylim( 0, 6 )
	ymean = np.repeat( np.mean( yi[:i+1] ), steps )
	ax[0][i].plot( xrange, ymean, "r--" )

	# plot S(a)
	ax[1][i].plot( a, S_plot )
	ax[1][i].set_xlabel( r"$a$")
	ax[1][i].set_ylabel( r"$S(a)$")
	ax[1][i].set_xlim( 0, 6 )
	ax[1][i].set_ylim( 0, 50 )
	ax[1][i].text( 0.5, 45, "$N=%d$" % (i+1) )

plt.show()

Wie in der Ausgabe des Codebeispiels zu sehen, wird die Parabel mit mehr Datenpunkten immer schmaler bzw. steiler. Die Krümmung der Parabel im Wertebereich um das Minimum könnte also ein geeignetes Maß für die Unsicherheit auf $\hat{a}$ sein. Mathematisch entspricht diese Krümmung der zweiten Ableitung von $S$ nach dem Parameter $a$:
$$
\begin{split}
S &= \sum_i \frac{(y_i-a)^2}{\sigma^2} \overset{!}{=} \mathsf{min},\\
\frac{\partial S}{\partial a} &= -2\sum_i\frac{y_i-a}{\sigma^2},\\
\frac{\partial^2 S}{\partial a^2} &= 2\sum_i\frac{1}{\sigma^2} = \frac{2N}{\sigma^2}.
\end{split}
$$
Im Falle von mehr als einem Parameter, also $\mathbf{a}=(a_i,\dots,a_m)^\mathsf{T}$, wird die zweite Ableitung durch die Matrix der zweiten partiellen Ableitungen (Hesse-Matrix, engl.: Hessian) ersetzt, siehe weiter unten.

Der Vergleich mit der Erwartung von oben zeigt, dass, zunächst für diesen Spezialfall, der Kehrwert der Varianz bis auf einen Faktor 1/2 der zweiten Ableitung von $S$ nach dem Parameter, also der Krümmung von $S$, entspricht:
$$
\frac{1}{2}\frac{\partial^2 S}{\partial a^2} = \frac{N}{\sigma^2}=
\frac{1}{\mathsf{V}[\hat{a}]} \equiv \mathsf{V}[\hat{a}]^{-1}.
$$

Dieser Zusammenhang zwischen Krümmung von $S$ und Kovarianzmatrix lässt sich auch ganz allgemein für die lineare LS-Methode zeigen. Die allgemeinste Form von $S$ für eine Modellfunktion linear in den Parametern ($\boldsymbol{\lambda}=\mathbf{Aa}$) ist
$$
S\equiv\chi^2\equiv
(\mathbf{y} - \mathbf{A}\mathbf{a})^\mathsf{T}\,
\mathbf{V}^{-1}\,
(\mathbf{y} - \mathbf{A}\mathbf{a}) \overset{!}=\mathsf{min}
$$
Der Gradient von $S$ bezüglich der Parameter $\mathbf{a}$ ergibt sich dann als
$$
\vec{\nabla}_\mathbf{a} S = 
-2\, \mathbf{A}^\mathsf{T}\,\mathbf{V}^{-1}\,\mathbf{y} +
2\, \mathbf{A}^\mathsf{T}\,\mathbf{V}^{-1}\,\mathbf{A}\,\mathbf{a}
$$ 
und die Matrix der zweiten partiellen Ableitungen am Minimum $\hat{\mathbf{a}}:$
$$
\left.
\frac{1}{2}\frac{\partial^2 S}{\partial a_i \, \partial a_j}\right|_\mathbf{\hat{a}} = 
(\mathbf{A}^\mathsf{T}\,
\mathbf{V}^{-1}\,
\mathbf{A})_{ij}. 
$$
Ein Vergleich mit der analytischen Rechnung zur Kovarianzmatrix am Anfang von Kapitel 4,
$$
\mathbf{V}[\hat{\mathbf{a}}] =
\mathbf{B}\mathbf{V}\mathbf{B}^\mathsf{T} = 
(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1},
$$
zeigt wiederum, dass
$$
\left.\frac{1}{2}\frac{\partial^2 S}{\partial a_i \, \partial a_j}\right|_\mathbf{\hat{a}} = 
(\mathbf{V}[\mathbf{\hat a}]^{-1})_{ij},
$$
dass also die Inverse der Kovarianzmatrix bis auf einen Faktor 1/2 der Hesse-Matrix von $S$ (ausgewertet am Minimum: $\mathbf{a}=\hat{\mathbf{a}}$) entspricht.

### Varianz: grafische Methode
Der Zusammenhang zwischen Varianz und Krümmung von $S$ am Minimum kann auch auf **grafische** Weise hergestellt werden. Wir gehen dabei zurück auf den Fall eines einzigen Parameters $a$. Das Ziel dabei ist es, direkt an der grafischen Darstellung von $S(a)$ die Varianz $\mathsf{V}[\hat{a}]$ bzw. Standardabweichung $\sigma_{\hat{a}}$ abzulesen. Dies wird erreicht, indem eine horizontale Linie in die Grafik eingezeichnet wird, deren Schnittpunkte mit $S(a)$ ein Intervall um $\hat{a}$ bilden, das $\sigma_{\hat{a}}$ entspricht. Der vertikale Abstand der horizontalen Linie vom Minimum ist gegeben durch
$$
 \Delta \chi^2 \equiv \Delta S \equiv S(a) - S(\hat{a}). 
$$
Für die weitere Diskussion nähern wir $S(a)$ durch eine Parabel, die wir durch eine Taylor-Entwicklung um das Minimum $\hat{a}$ erhalten, die wir nach dem quadratischen Glied abbrechen:
$$
S(a) \approx S(\hat{a}) + 
\left.\frac{\partial S(a}{\partial a}\right|_{\hat a_i} (a - \hat{a}) +
\frac{1}{2} \left.\frac{\partial^2 S(a)}{\partial a^2}\right|_{\hat a} (a - \hat{a})^2 =
S(\hat{a}) + 
\frac{1}{2} \left.\frac{\partial^2 S(a)}{\partial a^2}\right|_{\hat a} (a - \hat{a})^2,
$$
wobei wir im zweiten Schritt verwendet haben, dass die erste Ableitung am Minimum verschwindet. Damit ist $\Delta\chi^2$ proportional zur zweiten Ableitung am Minimum:
$$
\Delta \chi^2 = \frac{1}{2} \left.\frac{\partial^2 S(a)}{\partial a^2}\right|_{\hat a} (a - \hat{a})^2.
$$
Mit dem Zusammenhang von zweiter Ableitung am Minimum und Varianz erhalten wir:
$$
\Delta \chi^2 = \frac{(a-\hat{a})^2}{\sigma_{\hat{a}}^2}.
$$
Für $\Delta \chi^2=1$ ergibt sich:
$$
\sigma_{\hat{a}}^2 = (a-\hat{a})^2 \quad\to\quad
a = \hat{a} \pm \sigma_{\hat{a}}.
$$
Das ist die grafische Lösung für die Standardabweichung: 
>Eine horizontale Linie im vertikalen Abstand von $\Delta \chi^2=1$ vom Minimum schneidet den Funktionsgraphen von $S(a)$ im Abstand von $\pm \sigma_{\hat{a}}$ von Minimum $\hat{a}$.

Das folgende Codebeispiel illustriert diesen Zusammenhang:

In [ ]:
"""least squares: graphical solution for variance"""
import numpy as np
import matplotlib.pyplot as plt

# true model parameters
atrue = 3
sig   = 1

# data points
N = 5
xi = np.linspace( 1, N, N )

# scan of a values
amin, amax, steps = 2, 4, 200
a = np.linspace( amin, amax, steps )

rng = np.random.default_rng( 42 )
yi = rng.normal( loc=atrue, scale=sig, size=N )

# plot
fig,ax = plt.subplots()

# compared to the code example above, this is an alternative way to compute S using list comprehension
S_plot = np.array( [ np.sum( ( ( yi - a_plot ) / sig )**2 ) for a_plot in a ] )

# this is a way to compute the minimum of the curve and the interval
S_min = S_plot.min()    # minimal value of S
i_min = S_plot.argmin() # index of minimal value
i_sigma, = np.where( S_plot < S_min+1 ) # range of indices where S is below S_min+1, first and last index are +/- 1 sigma

ax.plot( a, S_plot )
ax.set_xlabel( r"$a$")
ax.set_ylabel( r"$S(a)$")
ax.set_xlim( amin, amax )
ax.set_ylim( 5, 12 )

ax.vlines( (a[i_min], a[i_sigma[0]], a[i_sigma[-1]]), 5, 10, linestyles="dashdot" )
ax.hlines( (S_min,S_min+1), amin, amax, linestyles="dashed" )

ax.text( 3.75, S_min+0.1, r"$\Delta \chi^2=0$" )
ax.text( 3.75, S_min+1.1, r"$\Delta \chi^2=1$" )
ax.text( a[i_min], 10.2, r"$\hat{a}$", ha="center")
ax.text( a[i_sigma[0]], 10.2, r"$\hat{a}-\sigma_{\hat{a}}$", ha="center")
ax.text( a[i_sigma[-1]], 10.2, r"$\hat{a}+\sigma_{\hat{a}}$", ha="center")

plt.show()

Die obige Überlegung funktioniert auch für Modellfunktionen, die von mehr als einem Parameter abhängen und/oder nichtlinear in den Parametern sind. In diesem Fall lautet die Taylor-Entwicklung:
$$
S(\mathbf{a}) \approx
S(\mathbf{\hat a}) +
\sum_i \left.\frac{\partial S(\mathbf{a})}{\partial a_i}\right|_{\hat a_i}
(a_i - \hat a_i) +
\sum_{i,j} \left.\frac{1}{2} \,\frac{\partial^2 S(\mathbf{a})}{\partial a_i \, \partial a_j}\right|_{\hat a_i, \hat a_j}
(a_i - \hat a_i)(a_j - \hat a_j).
$$
Am Minimum $\mathbf{a}=\hat{\mathbf{a}}$ verschwinden alle ersten partiellen Ableitungen und die Matrix der zweiten partiellen Ableitungen (Hesse-Matrix) entspricht der inversen Kovarianzmatrix $\mathbf{V}[\mathbf{\hat a}]^{-1}$. 

>**Ausblick**: Die grafische Methode zur Schätzung der Varianz funktioniert nicht nur für die LS-Methode, sondern auch für die allgemeinere Maximum-Likelihood-Methode.

>**Exkurs: Was ist ein Unsicherheitsbalken ("Fehlerbalken")?**
>
>Nach obigen Überlegungen zur Schätzung der Varianz lohnt es sich, noch einmal auf die Bedeutung des Unsicherheitsbalkens zur Beschreibung der Unsicherheit eines Schätzwerts zurückzukehren. Die Angabe von Schätzwert und Unsicherheit $\hat{a} \pm \sigma_{\hat{a}}$ wird dabei grob interpretiert als Intervall, das "68,3% Wahrscheinlichkeit abdeckt". In der frequentistischen Statistik ist die genaue Interpretation: 68,3% aller aus unterschiedlichen Stichproben berechneten Intervalle $\hat{a} \pm \sigma_{\hat{a}}$ beinhalten den wahren Wert $a$. In dieser Sichtweise ist der **Unsicherheitsbalken dem Datenpunkt zugeordnet**. 
>
>Es ist aber auch eine andere Sichtweise auf Unsicherheitsbalken denkbar, bei der der **Unsicherheitsbalken dem wahren Wert zugeordnet** wird (bzw. der Modellfunktion). Der Datenpunkt besitzt in dieser Sichtweise keine Unsicherheit ("die Daten sind die Daten"). Diese Sichtweise entspricht unserem Modell einer Messung, bei der der wahre Wert durch zufällige Beiträge verschmiert wird. Damit folgen die Schätzwerte $\hat{a}$ einer bestimmten Wahrscheinlichkeitsverteilung im Parameterraum $f(\hat{a};a)$, z. B. einer Normalverteilung. Diese Verteilung lässt sich durch eine Variablentransformation in eine Verteilung $g(y_i;\lambda_i)$ der Messwerte $y_i$ um die Werte der Modellfunktion $\lambda_i$ an der Position $x_i$ übersetzen. Zu dieser Sichtweise passt auch, dass die Varianz $\sigma_i^2$ bzw. die Kovarianzmatrix $\mathbf{V}$, die in die LS-Methode eingeht, eigentlich die Varianz des wahren Wertes ist und – falls nicht bekannt – über die Varianz der Einzelmessung geschätzt werden muss. 
>
>Die folgende Abbildung vergleicht beide Sichtweisen:
><img src="img/uncertainty_bar.png" width=80%>

### Varianz: Pseudoexperimente
In vielen Fällen lässt die Varianz auch über eine Methode schätzen, die auf Zufallszahlen beruht. Die Idee ist, die Messung und ihre Unsicherheiten am Computer nachzustellen. Aus diesem Grund wird diese Methode häufig als Methode der **Pseudoexperimente** bezeichnet, auch als Ensembletests oder Toy-Monte-Carlo-Methode. Wir nehmen dazu an, dass die Modellfunktion den wahren Werten entspricht und die Wahrscheinlichkeitsverteilung der Unsicherheiten bekannt ist. Dieser Ansatz ähnelt unserem Modell einer Messung, bei dem Messungen am Computer simuliert werden, indem zum wahren Wert ein zufälliger Beitrag aus einer bekannten Wahrscheinlichkeitsverteilung (z. B. Normalverteilung) addiert wird: $m=w+z$. Der Unterschied besteht darin, dass für die Pseudoexperimente der wahre Wert nicht bekannt ist, sondern durch den Messwert aus der realen Messung ersetzt wird. Für eine Schätzung der Varianz ist dies irrelevant, denn es wird nur die Streuung um den Messwert betrachtet.

Der Vorteil der Varianzschätzung über Pseudoexperimente ist, dass sie (bei bekannten Wahrscheinlichkeitsverteilungen) **exakt** ist und häufig **mit wenig Aufwand implementiert** werden kann. Ein Nachteil ist der verhältnismäßig hohe Rechenaufwand – es handelt sich in gewisser Weise um eine "brute force"-Methode, siehe auch den Exkurs zur Nachhaltigkeit im Computing weiter unten. Auch die Fehlerfortpflanzung lässt sich mit Pseudoexperimenten exakt und einfach implementierbar umsetzen, siehe Beispiel zur Unsicherheit des Verhältnisses zweier Zufallsvariablen in Kapitel 2.

Im folgenden Codebeispiel soll die Unsicherheit einer Anpassung mithilfe von Pseudoexperimenten bestimmt werden. An zehn Messwerte mit Unsicherheiten in $x$ und $y$ wird eine Gerade angepasst. Gesucht sind die Unsicherheiten auf Steigung und $y$-Achsenabschnitt und deren (Anti-)Korrelation bei bekannten normalverteilten Unsicherheiten der Messwerte. Aus den zehn realen Messwerten ziehen wir jetzt 1000 Mal ein neues Pseudoexperiment mit jeweils zehn simulierten Messwerten. Für jeden simulierten Messwert wird der real gemessene Wert als wahrer Wert angenommen und um einen zufälligen Beitrag in $x$ und $y$ verschoben. Dann wird eine Anpassung mit `kafe2.xy_fit()` durchgeführt und die Parameterwerte histogrammiert. Dabei werden nur die Daten der Pseudoexperimente verwendet, aber nicht die Unsicherheiten aus den Anpassungen. Dennoch können aus der Standardabweichung der Histogramme die Unsicherheiten von Steigung und $y$-Achsenabschnitt und aus dem Korrelationskoeffizienten des Streudiagramms die Korrelation dieser Parameter bestimmt werden. Die Mittelwerte der Histogramme entsprechen natürlich den realen Messwerten, die in die Pseudoexperimente hineingesteckt wurden.

In [ ]:
"""Using kafe2 for a straight line fit in the laboratory course
uncertainties determined from pseudoexperiments (or: toy MC)"""

import numpy as np
import matplotlib.pyplot as plt
from PhyPraKit import generateXYdata 
from kafe2 import xy_fit, plot

# range of values
n, xmin, xmax = 10, 1., 10.
xdata = np.linspace( xmin, xmax, n )

def lin_model( x, a0=1., a1=1. ):
	'''linear model (straight line)'''
	return a0 + a1*x
	
# true parameter values	
lin_modell_pars = [ 1.0, 0.3 ]

# absolute uncertainty for x value, relative uncertainty for y
ey_rel = 0.1
ex = 0.3

# generate synthetic data according to linear model
xtrue, ytrue, ydata = generateXYdata( xdata, lin_model, ex, 0., srely=ey_rel, mpar=lin_modell_pars )
ey = ey_rel * ytrue 

# generate Npe pseudoexperiments
rng = np.random.default_rng( 42 )
Npe = 1000
par = np.zeros( (Npe, 2) )

for i in np.arange( Npe ):
	"""new pseudoexperiment: draw random x and y values from Gaussian distribution
	using mu = measured value and sigma = given uncertainty and fit these synthetic data points"""
	xpe = rng.normal( size=n, loc=xdata, scale=ex )
	ype = rng.normal( size=n, loc=ydata, scale=ey )
	result = xy_fit( lin_model, xpe, ype, x_error=ex, y_error=ey, save=False )
	par[i] = result['fit'].parameter_values

a0, a1 = par[:,0], par[:,1]
fig,ax = plt.subplots( 2, 2, figsize=(12,10) )

ax[0][0].hist( a0 )
ax[0][0].set_xlabel( r"$a_{0}$" )
ax[0][0].set_ylabel( "Frequency" )
ax[0][0].text(0.66, 0.85, r"$\hat{\mu} = $%5.3f %s$\hat\sigma = $%5.3f" % (np.mean( a0 ), "\n", np.std( a0, ddof=1 ) ), transform=ax[0][0].transAxes, backgroundcolor='white')

ax[1][1].hist( a1 )
ax[1][1].set_xlabel( r"$a_{1}$" )
ax[1][1].set_ylabel( "Frequency" )
ax[1][1].text(0.66, 0.85, r"$\hat{\mu} = $%5.3f %s$\hat\sigma = $%5.3f" % (np.mean( a1 ), "\n", np.std( a1, ddof=1 ) ), transform=ax[1][1].transAxes, backgroundcolor='white')

ax[1][0].scatter( a1, a0 )
ax[1][0].set_xlabel( r"$a_{1}$" )
ax[1][0].set_ylabel( r"$a_{0}$" )
ax[1][0].text(0.66, 0.85, r"$\hat{\rho} = $%5.3f" % np.corrcoef( a1, a0 )[1][0], transform=ax[1][0].transAxes, backgroundcolor='white')

xline = np.linspace( xmin-0.5, xmax+0.5, 200 )
result = xy_fit( lin_model, xtrue, ytrue, x_error=ex, y_error=ey, save=False )

# kafe2 fit returns parameter estimates
pardata = result['fit'].parameter_values
ax[0][1].errorbar( xdata, ydata, xerr=ex, yerr=ey, fmt='bo' )
ax[0][1].plot( xline, lin_model( xline, *pardata ), 'r--' )
ax[0][1].set_xlabel( r"$x$" )
ax[0][1].set_ylabel( r"$y$" )

# kafe2 fit also returns asymmetric uncertaintties and correlation matrix
parunc  = result['fit'].asymmetric_parameter_errors
parcorr = result['fit'].parameter_cor_mat
ax[1][0].text(0.60, 0.10, r"$a_0 = %5.3f^{+%5.3f}_{%5.3f}$%s$a_1 = %5.3f^{+%5.3f}_{%5.3f}$%s$\rho = %5.3f$" % (pardata[0],parunc[0][1],parunc[0][0],"\n",pardata[1],parunc[1][1],parunc[1][0],"\n",parcorr[1][0]), transform=ax[0][1].transAxes, backgroundcolor='white')

plt.show()

>**Exkurs: Computing und Nachhaltigkeit**
>
>Die Rechenleistung moderner Computer hat Methoden wie Pseudoexperimente (oder auch maschinelles Lernen) einfach zugänglich gemacht. Die 1000 Pseudoexperimente haben auf einem Laptop aus dem Jahr 2022 ca. 16 Sekunden benötigt. Dennoch ist dieser Aufwand zur Bestimmung der Unsicherheit viel höher als der für eine einzige Anpassung an die Daten und eine Abschätzung der Kovarianzmatrix aus dieser Anpassung. Wie in anderen Bereichen des Lebens sollte auch in der Wissenschaft auf den Verbrauch von Ressourcen geachtet werden – effizienter Computercode und ressourcenschonende Methoden tragen dazu bei.
>
>Dies ist unter anderem auch relevant bei Anfragen auf Suchmaschinen oder der Nutzung von generativen KI-Methoden, wie sie z. B. in ChatGPT angewendet werden. Für eine typische ChatGPT-Anfrage wird derzeit (2025) eine Energie von 1 bis 10 Wattstunden geschätzt, etwa zehnmal so viel wie für eine Anfrage bei Google. Dazu kommt der Energieeinsatz beim Training der KI-Modelle. Für 100 Tage Training von GPT4 wurden im Jahr 2024 Werte jenseits von 50 GWh geschätzt.
>
>Eine aktuelle Anekdote dazu: Am 17. April 2025 hat z. B. OpenAI-Chef Sam Altman auf der Plattform X auf die Frage, wie viel Geld Höflichkeitsfloskel wie "Please" und "Thank you" in ChatGPT kosten, als Antwort gegegen: “Tens of millions of dollars well spent — you never know.” 

### Korrelierte Unsicherheiten
In einer Dimension wird das Intervall $\pm1\sigma$ der Normalverteilung als Basis für die Angaben von Unsicherheiten einer Zufallsvariable verwendet. In der grafischen Methode wurde dazu die Summe der Residuenquadrate $S$ um das Minimum betrachtet und das $1\sigma$-Intervall mit der Regel $\Delta S\equiv\Delta\chi^21$ konstruiert.

In mehr als einer Dimension sind Zufallsvariablen im allgemeinen **korreliert**. Wie oben gezeigt, tritt eine solche Korrelation bereits für Steigung und Achsenabschnitt einer einfachen Ausgleichsgeraden auf. 
Daher sollte für mehr als eine Zufallsvariable anstatt des $1\sigma$-Intervalls idealerweise die vollständige Kovarianzmatrix angegeben werden. Leider ist dies in der Praxis (zu) häufig nicht der Fall und Korrelationen werden sogar komplett ignoriert. 

Um die Elemente der Kovarianzmatrix anschaulich grafisch darzustellen, bietet es sich an, die korrelierten Unsicherheiten von Paaren von Zufallsvariablen darzustellen. Daher soll hier deren funktionale Form explizit gegeben werden. Die Rolle, die in einer Dimension der Skalierungsparameter $\sigma$ einer univariaten Normalverteilung einnimmt, wird in zwei Dimensionen durch die Matrix $\boldsymbol{\Sigma}$ der bivariaten Normalverteilung (Zusatzmaterial in Kapitel 2) eingenommen:
$$
\boldsymbol{\Sigma} =
\begin{pmatrix}
\sigma_1^2 & \rho_{12} \,\sigma_1\sigma_2 \\
\rho_{12} \,\sigma_1\sigma_2 & \sigma_2^2 
\end{pmatrix}.
$$
In der Normalverteilung wird die Determinante von $\boldsymbol{\Sigma}$,
$$
\det\boldsymbol{\Sigma} = \sigma_1^2 \sigma_2^2 ( 1 - \rho_{12}^2),
$$ 
und ihre Inverse,
$$
\boldsymbol{\Sigma}^{-1} =
\frac{1}{\sigma_1^2 \sigma_2^2 (1-\rho_{12}^2)}
\begin{pmatrix}
\sigma_2^2 & -\rho_{12} \,\sigma_1\sigma_2 \\
-\rho_{12} \,\sigma_1\sigma_2 & \sigma_1^2 
\end{pmatrix},
$$
benötigt. Damit ergibt sich als zweidimensionale PDF:
$$
\begin{split}
&f(x_1, x_2; \mu_1, \mu_2, \sigma_1, \sigma_2, \rho_{12}) = 
\,\frac{1}{2\pi} \cdot
\frac{1}{\sigma_1\sigma_2\sqrt{1-\rho_{12}^2}} \cdot\\
&\exp\left[
-\frac{1}{2(1-\rho_{12}^2)}
\left[
\left(
\frac{x_1 - \mu_1}{\sigma_1}
\right)^2 +
\left(
\frac{x_2 - \mu_2}{\sigma_2}
\right)^2
- 2\rho_{12}
\left(
\frac{x_1 - \mu_1}{\sigma_1}
\right)
\left(
\frac{x_2 - \mu_2}{\sigma_2}
\right)
\right]
\right].
\end{split}
$$
Wir suchen das zweidimensionale Analogon zum $1\sigma$-Intervall. Dies erhalten wir, wenn wir fordern, dass der Exponent in dieser Gleichung gleich Eins ist. Dies ist erfüllt, wenn
$$
\left(
\frac{x_1 - \mu_1}{\sigma_1}
\right)^2 +
\left(
\frac{x_2 - \mu_2}{\sigma_2}
\right)^2
- 2\rho_{12}
\left(
\frac{x_1 - \mu_1}{\sigma_1}
\right)
\left(
\frac{x_2 - \mu_2}{\sigma_2}
\right)
= 2(1-\rho_{12}^2).
$$

Geometrisch bilden wir damit eine "Höhenlinie" in einer dreidimensionalen Darstellung der Funktion. Die Gleichung für die Höhenlinie entspricht einer geneigten Ellipse, die als **Kovarianzellipse** bezeichnet wird und hier schematisch abgebildet ist (Bildquelle: Glen Cowan, [Particle Data Group 2023](https://pdg.lbl.gov/2023/reviews/rpp2023-rev-statistics.pdf))

<img src="img/covariance_ellipse.png" width=50%>

Der Neigungswinkel der großen Hauptachse dieser Ellipse relativ zur $x_1$-Achse beträgt
$$
\tan 2\phi = 
\frac{2\rho_{12}\,\sigma_1\sigma_2}
{\sigma_2^2 - \sigma_1^2}.
$$
Für mehr als zwei Zufallsvariable werden für jedes Paar von Variablen Kovarianzellipsen gebildet. Die Fläche innerhalb der Kovarianzellipse entspricht dann einer Wahrscheinlichkeit von 39.3% (und nicht 68,3%, siehe Exkurs). Daher ist immer zu prüfen, ob es sich um ein zweidimensionales $1\sigma$-Intervall oder um ein zweidimensionales 68,3%-Intervall handelt.


>**Exkurs: Wahrscheinlichkeit in $n$ Dimensionen**
> 
> Wie das Wahrscheinlichkeitsintervall von $\pm1\sigma$ der Normalverteilung in einer Dimension kann auch in $n$ Dimensionen das Volumen innerhalb des $n$-dimensionalen Kovarianzellipsoiden einer Wahrscheinlichkeit zugeordnet werden. Der Ausdruck im Exponenten der PDF der multivariaten Normalverteilung $((\mathbf{x} - \boldsymbol{\mu})^\mathsf{T} \boldsymbol{\Sigma}^{-1} (\mathbf{x}- \boldsymbol{\mu}))^{1/2} $ wird auch als Mahalanobis-Abstand bezeichnet. Es kann gezeigt werden, dass für Normalverteilung in $n$ Dimensionen die Wahrscheinlichkeit innerhalb eines Mahalanobis-Abstands von $t\sigma$ gegeben ist durch eine $\chi^2$-Verteilung mit $n$ Freiheitsgraden. Für $n=2$ ist dann $\chi^2(t;2) = 1 - \exp[-t^2/2]$, also $P=0.393$ für $t=1$ und $P=0.865$ für $t=2$.

Im folgenden Codebeispiel mit dem Paket [`kafe2`](https://kafe2.readthedocs.io/en/latest/) wird eine Kovarianzellipse für eine nichtlineare Anpassung mit der Methode der kleinsten Quadrate gezeigt.

In [ ]:
"""demonstration of covariance ellipse for an LS fit in kafe2
based on an example from the kafe2 Beginners' Guide"""

#magic command needed to display plots inline
%matplotlib ipympl

import numpy as np
from kafe2 import xy_fit, plot, ContoursProfiler

def exponential_model(x, A_0=1., x_0=5.):
    """exponential function to model the data"""
    return A_0 * np.exp(x/x_0)

# data points with fixed absolute x uncertainty and relative y uncertainty
x_data = np.array( [0.38, 0.83, 1.96, 2.82, 4.28, 4.69, 5.97, 7.60, 7.62, 8.81, 9.87, 10.91] )
y_data = np.array( [1.60, 1.66, 2.12, 3.05, 3.57, 4.65, 6.21, 7.57, 8.27, 10.79, 14.27, 18.48] )
x_error = 0.3
y_error_rel = 0.02 * y_data

# Call kafe2 to fit data to exponential model (profile=True gives the error ellipse)
result=xy_fit( exponential_model, x_data, y_data, x_error=x_error, y_error_rel=y_error_rel, profile=True, save=False )
pl = plot( x_label="$x$", y_label="$A$", save=False )

# Call profile plot explicitly (otherwise the plot would not show inline)
# (in standalone scripts plot(plot_profile=True) would be sufficient)
cpl = ContoursProfiler( result['fit'] )
cpl.plot_profiles_contours_matrix()